In [1]:
import pandas as pd
import numpy as np
import math
import datetime
#import tensorflow as tf

In [5]:
user_index={}  # user编号，从0开始
position_index={}  # position编号，从0开始
link_out={}  # user到position的邻接矩阵
link_in={}  # position到user的邻接矩阵
user_trans_matrix=np.matrix(0)
position_matrix=np.matrix(0)
user_sim_matrix=np.matrix(0)  # user之间的相似度矩阵
position_sim_matrix=np.matrix(0)  # position之间的相似度矩阵
user_damp=0.8  # user阻尼系数
position_damp=0.8  # position阻尼系数
user_evidence_matrix=np.matrix(0)
position_evidence_matrix=np.matrix(0)

df=pd.read_csv(r'C:\Users\JDD\Downloads\1110title.csv')
df=df.loc[df['c_title'].notna()]
title_dict=dict()
for i in df.index:
    itemid=df['itemid'][i]
    title=df['c_title'][i]
    title_dict[str(itemid)]=title

In [13]:
def indexUserAndPosition():
    '''
    读取user浏览position页面的记录文件，为user和position建立编号
    '''
    global user_index
    global position_index
    user_count=0
    position_count=0
    df=pd.read_csv(r'C:\Users\JDD\Downloads\11107天.csv')
    df=df.sample(10000,random_state=23)
    for i in df.index:
        user=df['deviceid'][i]
        if user not in user_index:
            user_index[user]=user_count
            user_count+=1
        item_list=df['list'][i].strip().split(',')
        for ele in item_list:
            if ele not in position_index:
                position_index[ele]=position_count
                position_count+=1

In [12]:
def readLink():
    '''
    读取user浏览position页面的记录文件，建构出度和入度邻接矩阵
    '''
    global link_out
    global link_in
    global position_index
    global user_index
    global user_trans_matrix
    global position_trans_matrix

    df=pd.read_csv(r'C:\Users\JDD\Downloads\11107天.csv')
    df=df.sample(10000,random_state=23)
    for i in df.index:
        user = df['deviceid'][i]
        userid = user_index[user]
        link_out.setdefault(userid,[])
        item_list=df['list'][i].strip().split(',')
        for item in item_list:
            itemid=position_index[item]
            if item not in link_out[userid]:
                link_out[userid].append(itemid)
            link_in.setdefault(itemid,[])
            link_in[itemid].append(userid)
    user_trans_matrix=np.zeros((len(position_index),len(user_index)))
    position_trans_matrix=np.zeros((len(user_index),len(position_index)))
    for user in link_out.keys():
        prob=1.0/len(list(set(link_out[user])))
        for position in link_out[user]:
            user_trans_matrix[position,user]=prob
    for position in link_in.keys():
        prob=1.0/len(list(set(link_in[position])))
        for user in link_in[position]:
            position_trans_matrix[user,position]=prob

In [42]:
'''
def evidenceMatrix():
    global link_in
    global link_out
    global user_index
    global position_index
    global user_evidence_matrix
    global position_evidence_matrix
    
    evd_list=[]
    evidence_index=0
    for i in range(100):
        evidence_index+=math.pow(0.5,i+1)
        evd_list.append(evidence_index)
        
    usernum=len(link_out)
    positionnum=len(link_in)
    user_evidence_matrix=np.identity(usernum)
    position_evidence_matrix=np.identity(positionnum)
    for u1,l1 in link_out.items():
        for u2,l2 in link_out.items():
            common=[x for x in l1 if x in l2]
            commonlen=len(common)
            if commonlen>len(evd_list):
                commonlen=len(evd_list)
            evd=evd_list[commonlen-1]
            user_evidence_matrix[u1,u2]=evd
    for p1,l1 in link_in.items():
        for p2,l2 in link_in.items():
            common=[x for x in l1 if x in l2]
            commonlen=len(common)
            evd=evd_list[commonlen]
            position_evidence_matrix[u1,u2]=evd
'''

In [8]:
def initSimMatrix():
    '''
    初始化相似度矩阵position_sim_matrix/user_sim_matrix
    '''
    global link_out
    global link_in
    global user_sim_matrix
    global position_sim_matrix
    global user_trans_matrix
    global position_trans_matrix

    usernum = len(link_out)  # user节点的数量
    positionnum = len(link_in)  # position节点的数量
    user_sim_matrix=np.identity(usernum)
    position_sim_matrix=np.identity(positionnum)

In [9]:
def updateSim():
    '''
    迭代更新相似度
    '''
    global link_out
    global link_in
    global user_sim_matrix
    global position_sim_matrix
    global user_damp
    global position_damp
    global user_trans_matrix
    global position_trans_matrix
        
    usernum = len(link_out)  # user节点的数量
    positionnum = len(link_in)
    user_sim_matrix=0.8*np.dot(np.dot(user_trans_matrix.transpose(),position_sim_matrix),user_trans_matrix)+0.2*np.identity(usernum)
    position_sim_matrix=0.8*np.dot(np.dot(position_trans_matrix.transpose(),user_sim_matrix),position_trans_matrix)+0.2*np.identity(positionnum)
#    for i in range(usernum):
#        user_sim_matrix[i,i]=1
#    for i in range(positionnum):
#        position_sim_matrix[i,i]=1

In [10]:
def simrank(iteration):
    starttime=datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')
    print(str(starttime),'init_sim_matrix:')
    indexUserAndPosition()
    readLink()
    initSimMatrix()
    print(position_sim_matrix)
    print(user_trans_matrix.shape)
    for i in range(iteration):
        finishtime=datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')
        print(str(finishtime),'iteration{}-sim_matrix:'.format(i+1),'--------------------------------------------->')
        updateSim()
        print(position_sim_matrix)
    endtime=datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')
    printResult()
    print(str(endtime),'计算结束')

In [11]:
def printResult():
    '''
    打印输出相似度计算结果
    '''
    global position_sim_matrix
    global position_index
    global title_dict
    
    f_out_user = open(r'C:\Users\JDD\Desktop\1110simrank.txt', "w",encoding='utf-8')
    for p1,p1id in position_index.items():
        if p1 in title_dict.keys():
            neighbour = []
            for p2,p2id in position_index.items():
                if p1id !=p2id:
                    sim = position_sim_matrix[p1id,p2id]
                    if sim == None:
                        sim = 0
                    if sim > 0:
                        neighbour.append((p2,sim))
            # 按相似度由大到小排序
            neighbour = sorted(
                neighbour, key=lambda x:x[1], reverse=True)
            for (u, sim) in neighbour[:50]:
                if u in title_dict.keys():
                    f_out_user.write(str(sim)+title_dict[p1]+'\t'+title_dict[u]+'\t'+p1+'\t'+u+'\n')
    f_out_user.close()

In [14]:
simrank(8)

2020-11-10 13:47:47 init_sim_matrix:
[[1. 0. 0. ... 0. 0. 0.]
 [0. 1. 0. ... 0. 0. 0.]
 [0. 0. 1. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 1. 0. 0.]
 [0. 0. 0. ... 0. 1. 0.]
 [0. 0. 0. ... 0. 0. 1.]]
(7187, 10000)
2020-11-10 13:47:49 iteration1-sim_matrix: --------------------------------------------->
[[2.21199610e-01 3.56912959e-03 2.65358429e-03 ... 1.14053700e-03
  1.32645982e-03 4.73316929e-04]
 [3.56912959e-03 2.14079290e-01 1.76331335e-03 ... 1.16131740e-03
  8.37863204e-04 3.77885791e-04]
 [2.65358429e-03 1.76331335e-03 2.10709417e-01 ... 3.65321230e-04
  6.46308661e-04 5.66697545e-04]
 ...
 [1.14053700e-03 1.16131740e-03 3.65321230e-04 ... 3.90476190e-01
  0.00000000e+00 7.43321719e-04]
 [1.32645982e-03 8.37863204e-04 6.46308661e-04 ... 0.00000000e+00
  3.95555556e-01 1.73441734e-03]
 [4.73316929e-04 3.77885791e-04 5.66697545e-04 ... 7.43321719e-04
  1.73441734e-03 3.75609756e-01]]
2020-11-10 13:48:27 iteration2-sim_matrix: --------------------------------------------->
[[0.21979943 

In [33]:
printResult()

In [36]:
test={}
df=pd.read_csv(r'C:\Users\JDD\Downloads\test_expose.csv')
for i in df.index:
    deviceid=df['deviceid'][i]
    test.setdefault(deviceid,{})
    j=df['list'][i]
    item_list=j.strip().split(',')
    test[deviceid]['expose']=item_list
df=pd.read_csv(r'C:\Users\JDD\Downloads\test_click.csv')
for i in df.index:
    deviceid=df['deviceid'][i]
    test.setdefault(deviceid,{})
    j=df['list'][i]
    item_list=j.strip().split(',')
    test[deviceid]['click']=item_list

In [117]:
sim_dict={}
for p1,p1id in position_index.items():
    neighbour = []
    sim_dict.setdefault(p1,{})
    for p2,p2id in position_index.items():
        if p1id !=p2id:
            sim = position_sim_matrix[p1id,p2id]
            if sim == None:
                sim = 0
            if sim > 0:
                neighbour.append((p2,sim))
    # 按相似度由大到小排序
    neighbour = sorted(neighbour, key=lambda x:x[1], reverse=True)
    for (u, sim) in neighbour[:50]:
        sim_dict[p1][u]=sim

{'1966599': {'3012268': 0.0016043861774634443,
  '2328873': 0.001356612799431538,
  '2361450': 0.0013520715067397782,
  '2474165': 0.001298287178870888,
  '3073715': 0.0012193910370277483,
  '2141790': 0.0011975726080106616,
  '2706573': 0.0011960756014993525,
  '3170594': 0.0011945631501469997,
  '2793458': 0.001148689233874081,
  '2986744': 0.0011370359853282283,
  '3116948': 0.001119614677134793,
  '2547306': 0.0011124847388348607,
  '3078740': 0.0010951524284023104,
  '2621223': 0.0010940916866331947,
  '2388083': 0.0010924115076256043,
  '2901621': 0.0010785426283640663,
  '3070272': 0.0010636554664093234,
  '2926524': 0.00105693564153265,
  '3106709': 0.0010480015192179948,
  '3254146': 0.0010281961897853386,
  '2817543': 0.0010264935128490842,
  '1959233': 0.0010242418599951022,
  '3149976': 0.0010144290920470005,
  '2294828': 0.0010032162660233086,
  '2492873': 0.0009979091340402522,
  '2442812': 0.000992191810764798,
  '1937833': 0.00099071012998714,
  '2062779': 0.00098613949

In [201]:
Sim_dict={}
for i in sim_dict.keys():
    Sim_dict.setdefault(i,{})
    min_score=np.min(list(sim_dict[i].values()))
    max_score=np.max(list(sim_dict[i].values()))
    for j in sim_dict[i].keys():
        score=(sim_dict[i][j]-min_score)/(max_score-min_score)
        Sim_dict[i][j]=score
Sim_dict

{'1966599': {'3012268': 1.0,
  '2328873': 0.6493349111280975,
  '2361450': 0.642907776711969,
  '2474165': 0.5667886784380968,
  '3073715': 0.4551296987251425,
  '2141790': 0.4242508310635135,
  '2706573': 0.42213216954507377,
  '3170594': 0.4199916494775025,
  '2793458': 0.35506788303204606,
  '2986744': 0.338575443572099,
  '3116948': 0.3139196688700682,
  '2547306': 0.30382891389285266,
  '3078740': 0.27929909464244485,
  '2621223': 0.2777978635186992,
  '2388083': 0.2754199643041131,
  '2901621': 0.2557918193539538,
  '3070272': 0.23472253414108443,
  '2926524': 0.2252121985017211,
  '3106709': 0.21256804431394705,
  '3254146': 0.18453824684012254,
  '2817543': 0.18212850708553566,
  '1959233': 0.17894182070937217,
  '3149976': 0.1650541497580671,
  '2294828': 0.149185025054941,
  '2492873': 0.14167402478818217,
  '2442812': 0.13358249497807348,
  '1937833': 0.1314855234401937,
  '2062779': 0.12501686503641896,
  '3105808': 0.12361401995252742,
  '3078752': 0.11528916564981503,
  '

In [137]:
def get_key(dct, value):
     return list(filter(lambda k:dct[k]==value,dct))

In [50]:
device_list=[x for x in user_index.keys() if x in test.keys()]
PRECISION=[]
RECALL=[]
expose_ACC=[]
for device in device_list:
    userid=user_index[device]
    rec_dict={}
    watch_list=link_out[userid]
    for itemid in watch_list:
        item=get_key(position_index,itemid)
        simdict=Sim_dict[item[0]]
        for sim_item,sim in Sim_dict.items():
            rec_dict[sim_item]=sim
    rec=sorted(rec_dict, key=lambda x:x[1], reverse=True)[:50]
    exposed=[x for x in rec if x in test[device]['expose']]
    if len(exposed)>0:
        if len(test[device].keys())==2:
            true=[x for x in rec if x in test[device]['click']]
            po=[x for x in test[device]['click'] if x in rec]
            acc=len(true)/len(rec)
            recall=len(po)/len(test[device]['click'])
            expose_acc=len(true)/len(exposed)
#        else:
#            precision=0
#            recall=0
#            expose_acc=0
            PRECISION.append(acc)
            RECALL.append(recall)
            expose_ACC.append(expose_acc)
print(np.mean(PRECISION),np.mean(RECALL),np.mean(expose_ACC),len(expose_ACC))

0.006546546546546547 0.05801313157961577 0.2431149222815889 1332


In [204]:
device_list=[x for x in user_index.keys() if x in test.keys()]
ACC=[]
RECALL=[]
expose_ACC=[]
for deviceid in device_list:
    rec_dict={}
    device=user_index[deviceid]
    scaned=link_out[device]
    for itemid in scaned:
        item=get_key(position_index,itemid)[0]
        if item in list(Sim_dict.keys()):
            YBB={x:Sim_dict[item][x] for x in list(Sim_dict[item].keys())}
            for k,v in YBB.items():
                if k in rec_dict.keys():
                    tmp_v=rec_dict[k]
                    rec_dict[k]=max(tmp_v,v)
                else:
                    rec_dict[k]=v
    rec_sorted=sorted(rec_dict.items(),key=lambda x:x[1], reverse=True)[:50]
    rec=[x[0] for x in rec_sorted]
    exposed=[x for x in rec if x in test[deviceid]['expose']]
    if len(exposed)>0:
        if len(test[deviceid])==2:
            true=[x for x in rec if x in test[deviceid]['click']]
            po=[x for x in test[deviceid]['click'] if x in rec]
            acc=len(true)/len(rec)
            recall=len(po)/len(test[deviceid]['click'])
            expose_acc=len(true)/len(exposed)
        else:
            acc=0
            recall=0
            expose_acc=0
        ACC.append(acc)
        RECALL.append(recall)
        expose_ACC.append(expose_acc)
print(np.mean(ACC),np.mean(RECALL),np.mean(expose_ACC),2*np.mean(RECALL)*np.mean(expose_ACC)/(np.mean(RECALL)+np.mean(expose_ACC)))

0.00596819457436857 0.06973275580639259 0.2397887062526913 0.10804502658402322


In [205]:
MAX=[]
for i in sim_dict.keys():
    max_score=np.max(list(sim_dict[i].values()))
    MAX.append(max_score)
np.max(MAX)

0.16691132481374804

In [208]:
a=MAX.sort(reverse=True)
a

In [209]:
MAX

[0.16691132481374804,
 0.16691132481374804,
 0.165087591197703,
 0.165087591197703,
 0.165087591197703,
 0.08714638198870568,
 0.08714638198870568,
 0.08397096604026322,
 0.08175470355392364,
 0.01604100262600731,
 0.014740053344854133,
 0.014740053344854133,
 0.011258216935814667,
 0.011179083278798664,
 0.010632464611868423,
 0.01063246461186842,
 0.010553995871269145,
 0.010553995871269145,
 0.009977079901052475,
 0.009977079901052475,
 0.009962412708515136,
 0.009629588067786823,
 0.009115741549530501,
 0.0091157415495305,
 0.00897356044454436,
 0.008557766247446278,
 0.008557766247446278,
 0.008388003196804996,
 0.008388003196804996,
 0.008205992802230154,
 0.008198506527358899,
 0.008198506527358899,
 0.008182187467581634,
 0.008168350471666834,
 0.008153162511030747,
 0.008123748514590422,
 0.007950780070843077,
 0.007806558766935899,
 0.007803169350368399,
 0.007522940966999913,
 0.007506375472853027,
 0.007367242820471411,
 0.007367242820471409,
 0.007306197276521068,
 0.00730

In [221]:
item='1919521'
itemid=position_index[item]
neb=link_in[itemid]
neb

[3250, 9560]

In [223]:
item='1919779'
itemid=position_index[item]
neb=link_in[itemid]
neb

[6461, 12004]

In [ ]:
for i in range(10):
    sim_dict[i].setdefault(i,{})
    for j in range(len(i)):
        score=sim_dict[i][j]
        sum_score=score-min_score/max_score-min_score
        Sim_dict[i][j]=sum_score
        for i in range():
            for i in range(10):
                if x in sim_dict.keys():
                    pass
                else:
                    continue